<a href="https://colab.research.google.com/github/param-jot/NLToSparql/blob/main/NamedEntityRec.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install -q -U trax
import trax
# Install JAX.
!pip install --upgrade jax
!pip install --upgrade jaxlib
!pip install --upgrade trax

In [2]:
from trax import layers as tl
import os # For os dependent functionalities
import numpy as np # For scientific computing
import pandas as pd # For basic data analysis
import random as rnd # For using random functions
!pip install datasets
from datasets import load_dataset


     |████████████████████████████████| 245kB 34.8MB/s 
     |████████████████████████████████| 122kB 50.6MB/s 
     |████████████████████████████████| 245kB 30.8MB/s 


In [3]:
data = pd.read_csv("dataset.csv",encoding = 'ISO-8859-1')
data = data.fillna(method = 'ffill')
data.head()

Sentence     Word  POS  PTag    Type
0  Sentence 1      NaN  NaN   NaN     NaN
1  Sentence 1       EU  NNP  B-NP   B-ORG
2  Sentence 1  rejects  VBZ  B-VP       O
3  Sentence 1   German   JJ  B-NP  B-MISC
4  Sentence 1     call   NN  I-NP       O

In [4]:
## Extract the 'Word' column from the dataframe
words = data.loc[:, "Word"]

## Convert into a text file using the .savetxt() function
np.savetxt(r'words.txt', words.values, fmt="%s")

In [7]:
import json
vocab = {}
with open('words.txt') as f:
  for i, l in enumerate(f.read().splitlines()):
    vocab[l] = i
  print("Number of words:", len(vocab))
  vocab['<PAD>'] = len(vocab)
  print(vocab)
  #file = open('vocab.subword', mode='w')
  json.dump(vocab, file)
  

Number of words: 23324
{'nan': 0, 'EU': 204065, 'rejects': 2, 'German': 217734, 'call': 209494, 'to': 219094, 'boycott': 196405, 'British': 219251, 'lamb': 374, '.': 219523, 'Peter': 219488, 'Blackburn': 92236, 'BRUSSELS': 212458, '1996-08-22': 50657, 'The': 218975, 'European': 218242, 'Commission': 217450, 'said': 219054, 'on': 219533, 'Thursday': 216974, 'it': 219045, 'disagreed': 25572, 'with': 218985, 'advice': 218107, 'consumers': 187433, 'shun': 31, 'until': 206797, 'scientists': 187687, 'determine': 216086, 'whether': 217944, 'mad': 187828, 'cow': 187829, 'disease': 212104, 'can': 218101, 'be': 218865, 'transmitted': 5228, 'sheep': 41191, 'Germany': 218742, "'s": 219124, 'representative': 187156, 'the': 219250, 'Union': 211558, 'veterinary': 187261, 'committee': 203917, 'Werner': 5280, 'Zwingmann': 5281, 'Wednesday': 217132, 'should': 215580, 'buy': 208122, 'sheepmeat': 5272, 'from': 218825, 'countries': 217328, 'other': 218400, 'than': 217943, 'Britain': 218771, 'scientific': 1

In [8]:
class Get_sentence(object):
    def __init__(self,data):
        self.n_sent=1
        self.data = data
        agg_func = lambda s:[(w,p,t) for w,p,t in zip(s["Word"].values.tolist(),
                                                     s["POS"].values.tolist(),
                                                     s["Type"].values.tolist())]
        self.grouped = self.data.groupby("Sentence").apply(agg_func)
        self.sentences = [s for s in self.grouped]
      

In [9]:
getter = Get_sentence(data)
sentence = getter.sentences

In [10]:
words = list(set(data["Word"].values))
words_tag = list(set(data["Type"].values))

word_idx = {w : i+1 for i ,w in enumerate(words)}
tag_idx =  {t : i for i ,t in enumerate(words_tag)}
print(words)
print(word_idx)
print(words_tag)
print(tag_idx)


[nan, 'itself', 'caring', 'cluster', 'pasta', 'Mohali', 'INDORE', 'bln', 'dealing', 'inebetude', '.Giuseppe', '0.469', '7-2-24-1', 'Escuredo', 'reinforced', 'repeal', 'Amazon', 'delight', '29/8/96', 'Gogele', 'Finance', 'confessional', '212-859-1646', '728-9559', 'Alex', 'culled', 'Italian', 'Hearts', 'Estonian', 'I.', '1-106', 'appeared', 'Fehervar', 'voting', 'appear', 'Brighton', '3M', 'accosts', 'signature', 'Wang', 'pipe', 'Taiwanese', '482-1003', 'corn', 'DAKOTA', '14-6', 'Robben', 'Wills', '1975-1979', 'unable', 'treated', 'intention', '900', 'movie', '902', 'pruned', 'Hapoel', '658/96', 'maintaining', 'immediate', '600000', 'defects', '4-7', 'Oracle', 'Golden', 'CAMPAIGN', 'recycled', 'Award-winning', '125', 'Helmut', 'Damein', '2383', 'Pearson', 'NAN', 'Vriesde', 'Egurugbe', 'position-squaring', '15th', 'shore', 'advantage', 'two-goal', 'dictatorship', 'experts', 'Hick', 'cleaning', 'Bundesliga', 'Batterby', 'meteorologist', 'defeats', 'reliable', 'killer', 'feel', 'Suspected'

In [12]:
X = [[word_idx[w[0]] for w in s] for s in sentence]
y = [[tag_idx[w[2]] for w in s] for s in sentence]
print(len(sentence))
print(X)
print(y)

16628
[[1, 3161, 12282, 22631, 16345, 12425, 5280, 2337, 5045, 6193], [6193, 20207, 15635, 4849, 12425, 17987, 7775, 11504, 5816, 19108, 3161, 19738, 10540, 179, 16954, 11448, 1922, 14108, 22533, 16232, 11448, 19595, 4691, 10237, 12301, 538, 22534, 12144, 18170, 538, 20722, 21784, 20845, 235, 12425, 20783, 22533, 6193], [6193, 10369, 3239, 16368, 4854, 1126, 8062, 4166, 11419], [16425, 4985], [5449, 17235, 19415, 2035, 14767, 19030, 16934, 17454, 7765, 22693], [22693, 11261, 20786, 10771, 14767, 9833, 16934, 11666, 10436], [10436, 5363, 7919, 17708, 14767, 19030, 16934, 14117, 7765, 22693], [22693, 3007, 4189, 14328], [14328, 4985], [4985, 14499, 15531, 15935, 10301, 422, 8852, 14748, 4123, 6193], [6193, 13391, 16093], [16093, 10301, 22766], [22766, 5523, 19969, 20448, 1694, 11448, 19108, 21044, 10959, 19738, 15669, 11673, 20554, 11448, 646, 1587, 21784, 10518, 15669, 20116, 22064, 7952, 19108, 11545, 9677, 17656, 1017, 9099, 11448, 21360, 18112, 12442, 21784, 20440, 11324, 19108, 1960

In [38]:
def data_generator(batch_size, x, y,pad, shuffle=False, verbose=False):

    num_lines = len(x)
    #print(x)
    #print("Number of lines")
    #print(num_lines)
    lines_index = [*range(num_lines)]
    if shuffle:
        rnd.shuffle(lines_index)
    
    index = 0 
    while True:
        buffer_x = [0] * batch_size 
        buffer_y = [0] * batch_size 
        print(batch_size)
        max_len = 0
        for i in range(batch_size):
            if index >= num_lines:
                index = 0
                if shuffle:
                    rnd.shuffle(lines_index)
            
            buffer_x[i] = x[lines_index[index]]
            buffer_y[i] = y[lines_index[index]]
            
            lenx = len(x[lines_index[index]])    
            if lenx > max_len:
                max_len = lenx                  
            
            index += 1

        X = np.full((batch_size, max_len), pad)
        print(batch_size)
        Y = np.full((batch_size, max_len), pad)
        print(batch_size)
        #print(X)
        #print(Y)

        for i in range(batch_size):
            x_i = buffer_x[i]
            y_i = buffer_y[i]
            #print(x_i)
            #print(y_i)
            for j in range(len(x_i)):

                X[i, j] = x_i[j]
                Y[i, j] = y_i[j]

        if verbose: print("index=", index)
        yield((X,Y))
        #print(X)
        #print(Y)

In [39]:
from sklearn.model_selection import train_test_split
x_train,x_test,y_train,y_test = train_test_split(X,y,test_size = 0.1,random_state=1)

In [40]:

def NERmodel(tags, vocab_size=23400, d_model = 50):

  model = tl.Serial(
    # tl.Embedding(vocab_size, d_model),
    trax.models.reformer.Reformer(vocab_size, d_model, ff_activation=tl.LogSoftmax),
    #change vocab to input vocab
    tl.Dense(tags),
    tl.LogSoftmax()
  )

  return model

In [41]:
model = NERmodel(tags = 17)

print(model)

Serial_in2_out2[
  Serial_in2_out2[
    Select[0,1,1]_in2_out3
    Branch_out2[
      []
      [Serial[
        PaddingMask(0)
      ], RemoveAxes12]
    ]
    Serial_in2_out2[
      Serial[
        Embedding_23400_512
        Dropout
        Serial[
          PositionalEncoding
        ]
      ]
      Dup_out2
      ReversibleSerial_in3_out3[
        ReversibleHalfResidualEncoderAttn_in3_out3[
          Serial[
            LayerNorm
          ]
          SelfAttention_in2
        ]
        ReversibleSwap_in2_out2
        ReversibleHalfResidualEncoderFF_in2_out2[
          Serial[
            LayerNorm
            Dense_2048
            Dropout
            LogSoftmax
            Dense_512
            Dropout
          ]
        ]
        ReversibleSwap_in2_out2
        ReversibleHalfResidualEncoderAttn_in3_out3[
          Serial[
            LayerNorm
          ]
          SelfAttention_in2
        ]
        ReversibleSwap_in2_out2
        ReversibleHalfResidualEncoderFF_in2_out2[
    

In [43]:
from trax.supervised import training

rnd.seed(33)

batch_size = 64

train_generator = trax.data.inputs.add_loss_weights(
    data_generator(batch_size, x_train, y_train,vocab['<PAD>'], True),
    id_to_mask=vocab['<PAD>'])
print(x_train)
print(y_train)
print(batch_size)

eval_generator = trax.data.inputs.add_loss_weights(
    data_generator(batch_size, x_test, y_test,vocab['<PAD>'] ,True),
    id_to_mask=vocab['<PAD>'])
print(vocab)
print(batch_size)
#train_generator = train_generator_fn()
#eval_generator = eval_generator_fn()

[[11408, 14770, 14270, 3891], [6193, 14622, 11324, 14565, 19738, 20995, 20551, 21784, 445, 3210, 9364, 11629, 20310, 13669, 2012, 9522, 11448, 19108, 9069, 7503, 21429, 13354, 14024, 14565, 11324, 19108, 20091, 1986, 19419, 19108, 7503, 3562, 11324, 7358, 6193], [5944, 2978, 3272, 20929, 14767, 1354, 16934, 18715], [6193, 14492, 20778, 11448, 16177, 4422], [1684, 6911, 9314, 20671, 3456, 14767, 16344, 16934, 3761, 6708, 7555, 14767, 19237, 2317, 16934], [6193, 3559, 13736, 22807, 4598, 17214, 14571, 14292, 12425, 10109, 13745, 1391, 22107, 21520, 19161, 6790, 4866, 18488, 15981, 16601, 16135, 4828, 18342, 5417, 2065, 12425, 11582, 6935, 6193], [4985, 1528, 9314, 7129, 7000, 14562, 23080, 14719, 7112, 511, 6193], [6193, 3559, 3393, 538, 243, 13693, 8139, 14965, 6056, 1671, 21496, 8746, 7775, 16521, 23295, 14907, 2264, 9354, 11324, 21784, 19639, 15942, 6193], [11816, 1750, 5944, 14767, 1300, 4841, 22863, 16091, 16934], [22205, 8417, 7037, 19419, 3044, 1027, 11448, 14470, 538, 11810, 787,

In [44]:
def train_model(model, train_generator, eval_generator, train_steps=1, output_dir='model'):
    train_task = training.TrainTask(
      train_generator,  
      loss_layer = tl.CrossEntropyLoss(), 
      optimizer = trax.optimizers.Adam(0.01), 
      n_steps_per_checkpoint=1
    )

    eval_task = training.EvalTask(
      labeled_data = eval_generator, 
      metrics = [tl.CrossEntropyLoss(), tl.Accuracy()], 
      n_eval_batches = 1
    )

    training_loop = training.Loop(
        model, 
        train_task, 
        eval_tasks = eval_task, 
        output_dir = output_dir) 

    training_loop.run(n_steps = train_steps)
    return training_loop

In [45]:
train_steps = 1
training_loop = train_model(model, train_generator, eval_generator, train_steps)

64
64
64
64
64
64


/usr/local/lib/python3.7/dist-packages/jax/lib/xla_bridge.py:304: UserWarning: jax.host_id has been renamed to jax.process_index. This alias will eventually be removed; please update your code.
  Args:
/usr/local/lib/python3.7/dist-packages/jax/lib/xla_bridge.py:317: UserWarning: jax.host_count has been renamed to jax.process_count. This alias will eventually be removed; please update your code.
  return get_backend(None).platform


64
64
64

Step      1: Total number of trainable weights: 58233749
Step      1: Ran 1 train steps in 542.74 secs
Step      1: train CrossEntropyLoss |  2.07065582
64
64
64
Step      1: eval  CrossEntropyLoss |  3.50025344
Step      1: eval          Accuracy |  0.86879432


Load model

In [46]:
import torch
import tensorflow as tf
#Loading
#gin.parse_config('/content/model/config.gin')

model = trax.models.reformer.Reformer(
    input_vocab_size=33300,
    d_model=512, d_ff=2048,
    n_heads=8, n_encoder_layers=6, n_decoder_layers=6,
    max_len=2048, mode='eval')

#Initialization

model.init_from_file('/content/model/model.pkl.gz',
                     weights_only=True)

#sample sentence
sentence = 'German call to boycott British lamb'
print(sentence)
#Encoding of a sentence
tokens = [word_idx[w] for w in sentence.split(" ")]      
print(type(tokens))
print(tokens) 

array_token = np.array(tokens)
print(type(array_token))

#array_tokens = np.array_split(tokens,3)
print(array_token)
print(torch.IntTensor(array_token))
# Decode from the Reformer
tokenized = array_token[None, :]  # Add batch dimension.
print("shape of an array: ", tokenized.shape)
print(batch_size)
print(tf.shape(tokenized))
print(type(tokenized))
print(tokenized)
print(torch.IntTensor(tokenized))
print(trax.supervised.decoding.autoregressive_sample(
    model, tokenized, temperature=0.0))
tokenized_translation = trax.supervised.decoding.autoregressive_sample(
    model, tokenized, temperature=0.0)
print(tokenized_translation)



German call to boycott British lamb
<class 'list'>
[22631, 16345, 12425, 5280, 2337, 5045]
<class 'numpy.ndarray'>
[22631 16345 12425  5280  2337  5045]
tensor([22631, 16345, 12425,  5280,  2337,  5045], dtype=torch.int32)
shape of an array:  (1, 6)
64
tf.Tensor([1 6], shape=(2,), dtype=int32)
<class 'numpy.ndarray'>
[[22631 16345 12425  5280  2337  5045]]
tensor([[22631, 16345, 12425,  5280,  2337,  5045]], dtype=torch.int32)


LayerError: ignored

In [ ]:

sentence = 'German call to boycott British lamb'
#Encoding of a sentence

tokens = [word_idx[w] for w in sentence.split(" ")]      

print(tokens) 
print(type(tokens))
tokens = np.array(tokens)
print(tokens)

batch_of_tokens = tokens[None, :]  # Add batch dimension.
print(type(batch_of_tokens))
print(batch_of_tokens)
tokenized_translation = trax.supervised.decoding.autoregressive_sample(model, batch_of_tokens, temperature=1.0)
print(tokenized_translation)